# Capstone Project - Finding a Place for new Restaurnt
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening an **Argentinian restaurant**, or **BBQ restaurant** in **Argentina**.

Argentina is well known with its great meat, and bbq restaurant. Speccificaly, there are some main cities in Argentina that became very tourist one, and have alot of restaurants, including ones that offer local argentinian food. Since there are lots of restaurants in Argentina, and lots of tourist cities, we will try to detect **locations that are not already crowded with restaurants, or with this spicific argentnian meat**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants near the city center (any type of restaurant)
* number of and distance to argentinian or BBQ restaurants near the city center

Following data sources will be needed to extract/generate the required information:
* CSV data for Argentina's main cities
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **geopy.geocoders**
* number of restaurants and their type and location in every city will be obtained using **Foursquare API**

#### Import the needed dependencies

In [2]:
import requests
from geopy.geocoders import Nominatim
import folium
import pandas as pd
import matplotlib.cm as cm
import matplotlib.colors as colors
import numpy as np
from sklearn.cluster import KMeans

### Cities Candidates
We will use a CSV file from the web page https://simplemaps.com/. This file contains data for 503 prominent cities in Argentina, including 'name', 'lat', 'lon', 'population' (updated to 2020) for each entry.

In [3]:
df = pd.read_csv('argentina.csv')
df

city       lat        lng    country iso2  \
0                Buenos Aires -34.60828 -58.372295  Argentina   AR   
1                     Córdoba -31.41670 -64.183300  Argentina   AR   
2                     Rosario -32.95750 -60.639400  Argentina   AR   
3       San Miguel de Tucumán -26.81670 -65.216700  Argentina   AR   
4               Mar del Plata -38.00000 -57.550000  Argentina   AR   
..                        ...       ...        ...        ...  ...   
498                 Camarones -44.79710 -65.709900  Argentina   AR   
499                  Puelches -38.14560 -65.914300  Argentina   AR   
500             Limay Mahuida -37.15920 -66.675100  Argentina   AR   
501  Antofagasta de la Sierra -26.05940 -67.406400  Argentina   AR   
502               Cuchillo Có -38.33330 -64.616700  Argentina   AR   

                           admin_name  capital  population  population_proper  
0    Buenos Aires, Ciudad Autónoma de  primary  16157000.0          3054300.0  
1                             Córdoba    admin   1329604.0          1329604.0  
2                            Santa Fe    minor   1193605.0          1193605.0  
3                             Tucumán    admin    605767.0           605767.0  
4                        Buenos Aires    minor    593337.0           593337.0  
..                                ...      ...         ...                ...  
498                            Chubut    minor         NaN                NaN  
499                          La Pampa    minor         NaN                NaN  
500                          La Pampa    minor         NaN                NaN  
501                         Catamarca    minor         NaN                NaN  
502                          La Pampa    minor         NaN                NaN  

[503 rows x 9 columns]

in order to reduce the number of interesting cities, we decided to look only at cities with population of at least 50K people

In [4]:
df = df[df['population_proper'] > 50000].loc[:,['city', 'lat', 'lng', 'capital', 'population_proper']]
df

city       lat        lng  capital  population_proper
0            Buenos Aires -34.60828 -58.372295  primary          3054300.0
1                 Córdoba -31.41670 -64.183300    admin          1329604.0
2                 Rosario -32.95750 -60.639400    minor          1193605.0
3   San Miguel de Tucumán -26.81670 -65.216700    admin           605767.0
4           Mar del Plata -38.00000 -57.550000    minor           593337.0
..                    ...       ...        ...      ...                ...
68              San Pedro -24.21960 -64.870000    minor            52068.0
69             Punta Alta -38.88000 -62.080000    minor            54730.0
71                Ushuaia -54.80720 -68.304400    admin            56956.0
72                   Azul -36.78330 -59.850000    minor            55728.0
75           Cruz del Eje -30.73330 -64.800000    minor            52172.0

[70 rows x 5 columns]

In [113]:
address = 'argentina'
# address = 'Centro, bariloche, argentina'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Argentina are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Argentina are -34.9964963, -64.9672817.


In order to get a relative magnitude of the population, we will use the normal of this column

In [7]:
list_size = df['population_proper'] / df['population_proper'].max()
df['pop_norm'] = list_size
df

city       lat        lng  capital  population_proper  \
0            Buenos Aires -34.60828 -58.372295  primary          3054300.0   
1                 Córdoba -31.41670 -64.183300    admin          1329604.0   
2                 Rosario -32.95750 -60.639400    minor          1193605.0   
3   San Miguel de Tucumán -26.81670 -65.216700    admin           605767.0   
4           Mar del Plata -38.00000 -57.550000    minor           593337.0   
..                    ...       ...        ...      ...                ...   
68              San Pedro -24.21960 -64.870000    minor            52068.0   
69             Punta Alta -38.88000 -62.080000    minor            54730.0   
71                Ushuaia -54.80720 -68.304400    admin            56956.0   
72                   Azul -36.78330 -59.850000    minor            55728.0   
75           Cruz del Eje -30.73330 -64.800000    minor            52172.0   

    pop_norm  
0   1.000000  
1   0.435322  
2   0.390795  
3   0.198333  
4   0.194263  
..       ...  
68  0.017047  
69  0.017919  
71  0.018648  
72  0.018246  
75  0.017081  

[70 rows x 6 columns]

We got 70 cities in Argentina that might be interesting.

Lets observe the map of Argentina with the corresponding size of circle of the cities

In [8]:
map_argentina = folium.Map(location=[latitude, longitude], zoom_start=3.5)

# add markers to df
for lat, lng, city, pop, size in zip(df['lat'], df['lng'], df['city'], df['population_proper'], df['pop_norm']):
    label = '{},\n {}'.format(city, pop)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5 * size + 3,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_argentina)  
    
map_argentina

In [9]:
CLIENT_ID = 'N0YWYR2EWEA2GRUSN24MBCLHF3F4P3L2KNBMUHGVEVSB1FRE' # your Foursquare ID
CLIENT_SECRET = 'KX25L0IQX0OVH3X1BYFA0YQF23V4BKFXX5WOFNPQ5GKNJNFX' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: N0YWYR2EWEA2GRUSN24MBCLHF3F4P3L2KNBMUHGVEVSB1FRE
CLIENT_SECRET:KX25L0IQX0OVH3X1BYFA0YQF23V4BKFXX5WOFNPQ5GKNJNFX


### Foursquare
Now that we have our cities, let's use Foursquare API to get info on restaurants.

We're interested in venues in 'food' category, but only those that are proper restaurants - coffe shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in our list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific **Argentinian restaurant** or **BBQ** category, as we need info in the city.

Also, we will check those venues within a **radius of 1000 meters** from the city center.

In [10]:
def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

In [11]:
def getNearbyRestaurants(names, latitudes, longitudes, category, radius=1000):
    """This function gets nearby restaurants from specific category for every city
        inputs: 
               "names", pandas series, city name
               "latitudes", pandas series, city lat
               "longitudes", pandas series, city lon
               "radius", =1000 by default
        output: 
               nearby_venues, pandas df with columns: ['City', 
                  'City Latitude', 
                  'City Longitude', 
                  'restaurant', 
                  'restaurant Latitude', 
                  'restaurant Longitude', 
                  'restaurant Category']
                  """
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng,
            category,
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['City', 
                  'City Latitude', 
                  'City Longitude', 
                  'restaurant', 
                  'restaurant Latitude', 
                  'restaurant Longitude', 
                  'restaurant Category']
    
    return(nearby_venues)

In [12]:
food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

argentina_venues = getNearbyRestaurants(df['city'],  df['lat'], df['lng'], food_category, radius=1000)

Buenos Aires
Córdoba
Rosario
San Miguel de Tucumán
Mar del Plata
Salta
San Juan
Lanús
Santa Fe
Corrientes
San Salvador de Jujuy
Bahía Blanca
Resistencia
Posadas
Santiago del Estero
Paraná
Merlo
Neuquén
Quilmes
Formosa
José C. Paz
Godoy Cruz
La Plata
La Rioja
Berazategui
Comodoro Rivadavia
San Luis
José María Ezeiza
San Nicolás de los Arroyos
Catamarca
Concordia
Florencio Varela
San Justo
San Martín
Tandil
Puerto Madryn
Mendoza
San Carlos de Bariloche
Villa Mercedes
Gualeguaychú
San Rafael
La Banda
Santa Rosa
Berisso
Morón
Zárate
Río Gallegos
Caseros
Rafaela
Pergamino
Campana
Presidencia Roque Sáenz Peña
Luján
Pilar
Necochea
Villa María
San Ramón de la Nueva Orán
Concepción del Uruguay
Goya
Reconquista
Las Heras
Oberá
San Francisco
Los Polvorines
Tartagal
San Pedro
Punta Alta
Ushuaia
Azul
Cruz del Eje


In [14]:
argentina_venues.rename(columns={'Neighborhood Latitude':'Latitude', 'Neighborhood Longitude': 'Longitude'}, inplace=True)

In [15]:
argentina_venues

City  City Latitude  City Longitude        restaurant  \
0     Buenos Aires      -34.60828      -58.372295          Pertutti   
1     Buenos Aires      -34.60828      -58.372295       London City   
2     Buenos Aires      -34.60828      -58.372295   Piazzolla Tango   
3     Buenos Aires      -34.60828      -58.372295           FuraiBo   
4     Buenos Aires      -34.60828      -58.372295       Adorado Bar   
...            ...            ...             ...               ...   
1051  Cruz del Eje      -30.73330      -64.800000        El Cantaro   
1052  Cruz del Eje      -30.73330      -64.800000  safari resto bar   
1053  Cruz del Eje      -30.73330      -64.800000         Pizza Uno   
1054  Cruz del Eje      -30.73330      -64.800000      Viejo Munich   
1055  Cruz del Eje      -30.73330      -64.800000         El Cardon   

      restaurant Latitude  restaurant Longitude     restaurant Category  
0              -34.609195            -58.373392  Argentinian Restaurant  
1              -34.608505            -58.374874                    Café  
2              -34.606099            -58.374899        Theme Restaurant  
3              -34.610105            -58.372549     Japanese Restaurant  
4              -34.611895            -58.373358                    Café  
...                   ...                   ...                     ...  
1051           -30.727358            -64.800040           Deli / Bodega  
1052           -30.726425            -64.803566             Pizza Place  
1053           -30.726104            -64.803277             Pizza Place  
1054           -30.736909            -64.791571       German Restaurant  
1055           -30.737260            -64.791606               BBQ Joint  

[1056 rows x 7 columns]

Now we'll add a column that contains the distance of the restaurant from the city center

In [16]:
import geopy.distance

def dist2center(center_coor, rest__coor):
    """calculate the distance of a restaurant from the city center
    inputs: center_coor, rest__coor - tuples(lat, lon)
    output: dist, float
    """
    return geopy.distance.distance(center_coor, rest__coor).m
    

In [17]:
dist_list = []
for center_lat, center_lon, rest_lat, rest_lon in zip(argentina_venues['City Latitude'], 
                                                      argentina_venues['City Longitude'], 
                                                      argentina_venues['restaurant Latitude'], 
                                                      argentina_venues['restaurant Longitude']):
    dist_list.append(dist2center((center_lat, center_lon),(rest_lat, rest_lon)))

# geopy.distance.distance(coords_1, coords_2).m

argentina_venues['dist2center'] = dist_list
argentina_venues

City  City Latitude  City Longitude        restaurant  \
0     Buenos Aires      -34.60828      -58.372295          Pertutti   
1     Buenos Aires      -34.60828      -58.372295       London City   
2     Buenos Aires      -34.60828      -58.372295   Piazzolla Tango   
3     Buenos Aires      -34.60828      -58.372295           FuraiBo   
4     Buenos Aires      -34.60828      -58.372295       Adorado Bar   
...            ...            ...             ...               ...   
1051  Cruz del Eje      -30.73330      -64.800000        El Cantaro   
1052  Cruz del Eje      -30.73330      -64.800000  safari resto bar   
1053  Cruz del Eje      -30.73330      -64.800000         Pizza Uno   
1054  Cruz del Eje      -30.73330      -64.800000      Viejo Munich   
1055  Cruz del Eje      -30.73330      -64.800000         El Cardon   

      restaurant Latitude  restaurant Longitude     restaurant Category  \
0              -34.609195            -58.373392  Argentinian Restaurant   
1              -34.608505            -58.374874                    Café   
2              -34.606099            -58.374899        Theme Restaurant   
3              -34.610105            -58.372549     Japanese Restaurant   
4              -34.611895            -58.373358                    Café   
...                   ...                   ...                     ...   
1051           -30.727358            -64.800040           Deli / Bodega   
1052           -30.726425            -64.803566             Pizza Place   
1053           -30.726104            -64.803277             Pizza Place   
1054           -30.736909            -64.791571       German Restaurant   
1055           -30.737260            -64.791606               BBQ Joint   

      dist2center  
0      142.875942  
1      237.840260  
2      340.024866  
3      203.750072  
4      412.681522  
...           ...  
1051   658.770026  
1052   835.195206  
1053   857.334495  
1054   900.942656  
1055   915.979304  

[1056 rows x 8 columns]

now, lets **remove all the venues that is not a restaurat type**:

In [19]:
list_of_venues = argentina_venues['restaurant Category'].unique()
matchers = ['argentinian','bbq', 'restaurant', 'diner', 'taverna', 'steakhouse']
matching = [s for s in list_of_venues if any(xs in s.lower() for xs in matchers)]

argentina_restaurants = argentina_venues[argentina_venues['restaurant Category'].isin(matching)]
argentina_restaurants

City  City Latitude  City Longitude           restaurant  \
0     Buenos Aires      -34.60828      -58.372295             Pertutti   
2     Buenos Aires      -34.60828      -58.372295      Piazzolla Tango   
3     Buenos Aires      -34.60828      -58.372295              FuraiBo   
7     Buenos Aires      -34.60828      -58.372295      Elauge Hermanos   
8     Buenos Aires      -34.60828      -58.372295   Bidou de la Merced   
...            ...            ...             ...                  ...   
1041       Ushuaia      -54.80720      -68.304400     Parrila La Rueda   
1043       Ushuaia      -54.80720      -68.304400               Bamboo   
1050          Azul      -36.78330      -59.850000  Parrilla El Carrito   
1054  Cruz del Eje      -30.73330      -64.800000         Viejo Munich   
1055  Cruz del Eje      -30.73330      -64.800000            El Cardon   

      restaurant Latitude  restaurant Longitude     restaurant Category  \
0              -34.609195            -58.373392  Argentinian Restaurant   
2              -34.606099            -58.374899        Theme Restaurant   
3              -34.610105            -58.372549     Japanese Restaurant   
7              -34.609276            -58.375499               BBQ Joint   
8              -34.605619            -58.373134              Restaurant   
...                   ...                   ...                     ...   
1041           -54.805330            -68.301049              Steakhouse   
1043           -54.805051            -68.299648      Chinese Restaurant   
1050           -36.789406            -59.858032               BBQ Joint   
1054           -30.736909            -64.791571       German Restaurant   
1055           -30.737260            -64.791606               BBQ Joint   

      dist2center  
0      142.875942  
2      340.024866  
3      203.750072  
7      313.927511  
8      305.112268  
...           ...  
1041   299.601331  
1043   388.071016  
1050   986.483509  
1054   900.942656  
1055   915.979304  

[535 rows x 8 columns]

In [20]:
list_of_venues

array(['Argentinian Restaurant', 'Café', 'Theme Restaurant',
       'Japanese Restaurant', 'Burger Joint', 'Salad Place', 'BBQ Joint',
       'Restaurant', 'Deli / Bodega', 'Bistro', 'Italian Restaurant',
       'Mediterranean Restaurant', 'Sandwich Place', 'French Restaurant',
       'Vegetarian / Vegan Restaurant', 'Venezuelan Restaurant',
       'Sushi Restaurant', 'Seafood Restaurant', 'Creperie',
       'Pizza Place', 'Steakhouse', 'Empanada Restaurant', 'Bakery',
       'Asian Restaurant', 'Chinese Restaurant', 'Gastropub',
       'American Restaurant', 'Donut Shop', 'Spanish Restaurant',
       'Fast Food Restaurant', 'Peruvian Restaurant', 'Breakfast Spot',
       'Turkish Restaurant', 'Diner', 'Middle Eastern Restaurant',
       'Comfort Food Restaurant', 'South American Restaurant',
       'Mexican Restaurant', 'African Restaurant', 'German Restaurant',
       'Bagel Shop', 'Food Stand', 'Snack Place',
       'Latin American Restaurant', 'Cafeteria', 'Food', 'Hot Dog Joint',


How many restaurants there are in each city:

In [21]:
argentina_restaurants.groupby('City').count()

City Latitude  City Longitude  restaurant  \
City                                                                      
Azul                                      1               1           1   
Bahía Blanca                             10              10          10   
Berazategui                               4               4           4   
Buenos Aires                             55              55          55   
Caseros                                   2               2           2   
Catamarca                                 8               8           8   
Comodoro Rivadavia                        4               4           4   
Concepción del Uruguay                    2               2           2   
Concordia                                 2               2           2   
Corrientes                                3               3           3   
Cruz del Eje                              2               2           2   
Córdoba                                  41              41          41   
Florencio Varela                          3               3           3   
Godoy Cruz                                6               6           6   
Goya                                      3               3           3   
Gualeguaychú                              4               4           4   
La Banda                                  3               3           3   
La Plata                                  4               4           4   
La Rioja                                  3               3           3   
Lanús                                     8               8           8   
Las Heras                                 2               2           2   
Luján                                     1               1           1   
Mar del Plata                            36              36          36   
Mendoza                                  56              56          56   
Merlo                                     6               6           6   
Morón                                    11              11          11   
Neuquén                                   4               4           4   
Oberá                                     1               1           1   
Paraná                                    3               3           3   
Pergamino                                 1               1           1   
Pilar                                     4               4           4   
Posadas                                  12              12          12   
Presidencia Roque Sáenz Peña              2               2           2   
Puerto Madryn                             6               6           6   
Punta Alta                                4               4           4   
Quilmes                                  17              17          17   
Reconquista                               4               4           4   
Resistencia                               9               9           9   
Rosario                                  23              23          23   
Río Gallegos                              2               2           2   
Salta                                    29              29          29   
San Carlos de Bariloche                  43              43          43   
San Juan                                  6               6           6   
San Justo                                 3               3           3   
San Luis                                  6               6           6   
San Miguel de Tucumán                     3               3           3   
San Nicolás de los Arroyos                4               4           4   
San Pedro                                 2               2           2   
San Rafael                                3               3           3   
San Ramón de la Nueva Orán                3               3           3   
San Salvador de Jujuy                     5               5           5   
Santa Fe                                  7            

In [22]:
print('There are {} uniques categories.'.format(len(argentina_restaurants['restaurant Category'].unique())))

There are 34 uniques categories.


Now, we will turn the categories into columns, and calculate the frequencies of each category in the vicinity of the city center: 

In [23]:
# one hot encoding
argentina_onehot = pd.get_dummies(argentina_restaurants[['restaurant Category']], prefix="", prefix_sep="")

# add City column back to dataframe
argentina_onehot['City'] = argentina_restaurants['City'] 

# move City column to the first column
fixed_columns = [argentina_onehot.columns[-1]] + list(argentina_onehot.columns[:-1])
argentina_onehot = argentina_onehot[fixed_columns]

argentina_onehot.shape

(535, 35)

In [24]:
argentina_grouped = argentina_onehot.groupby('City').mean().reset_index()
argentina_grouped

City  African Restaurant  American Restaurant  \
0                           Azul             0.00000             0.000000   
1                   Bahía Blanca             0.00000             0.000000   
2                    Berazategui             0.00000             0.000000   
3                   Buenos Aires             0.00000             0.018182   
4                        Caseros             0.00000             0.000000   
5                      Catamarca             0.00000             0.000000   
6             Comodoro Rivadavia             0.00000             0.000000   
7         Concepción del Uruguay             0.00000             0.000000   
8                      Concordia             0.00000             0.000000   
9                     Corrientes             0.00000             0.000000   
10                  Cruz del Eje             0.00000             0.000000   
11                       Córdoba             0.02439             0.024390   
12              Florencio Varela             0.00000             0.000000   
13                    Godoy Cruz             0.00000             0.166667   
14                          Goya             0.00000             0.000000   
15                  Gualeguaychú             0.00000             0.000000   
16                      La Banda             0.00000             0.000000   
17                      La Plata             0.00000             0.000000   
18                      La Rioja             0.00000             0.000000   
19                         Lanús             0.00000             0.000000   
20                     Las Heras             0.00000             0.000000   
21                         Luján             0.00000             0.000000   
22                 Mar del Plata             0.00000             0.000000   
23                       Mendoza             0.00000             0.000000   
24                         Merlo             0.00000             0.000000   
25                         Morón             0.00000             0.000000   
26                       Neuquén             0.00000             0.000000   
27                         Oberá             0.00000             0.000000   
28                        Paraná             0.00000             0.000000   
29                     Pergamino             0.00000             0.000000   
30                         Pilar             0.00000             0.000000   
31                       Posadas             0.00000             0.000000   
32  Presidencia Roque Sáenz Peña             0.00000             0.000000   
33                 Puerto Madryn             0.00000             0.000000   
34                    Punta Alta             0.00000             0.000000   
35                       Quilmes             0.00000             0.058824   
36                   Reconquista             0.00000             0.000000   
37                   Resistencia             0.00000             0.000000   
38                       Rosario             0.00000             0.000000   
39                  Río Gallegos             0.00000             0.000000   
40                         Salta             0.00000             0.000000   
41       San Carlos de Bariloche             0.00000             0.000000   
42                      San Juan             0.00000             0.000000   
43                     San Justo             0.00000             0.000000   
44                      San Luis             0.00000             0.000000   
45         San Miguel de Tucumán             0.00000             0.000000   
46    San Nicolás de los Arroyos             0.00000             0.000000   
47                     San Pedro             0.00000             0.000000   
48                    San Rafael             0.00000             0.000000   
49    San Ramón de la Nueva Orán             0.00000             0.000000   
50         San Salvador de Jujuy             0.00000             0.000000   
51                      

Lets print the top 10 restaurant types in each city:

In [25]:
num_top_venues = 10

for city in argentina_grouped['City']:
    print("----"+city+"----")
    temp = argentina_grouped[argentina_grouped['City'] == city].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Azul----
                       venue  freq
0                  BBQ Joint   1.0
1         African Restaurant   0.0
2                 Steakhouse   0.0
3          Paella Restaurant   0.0
4        Peruvian Restaurant   0.0
5                 Restaurant   0.0
6         Seafood Restaurant   0.0
7  South American Restaurant   0.0
8         Spanish Restaurant   0.0
9           Sushi Restaurant   0.0


----Bahía Blanca----
                       venue  freq
0     Argentinian Restaurant   0.3
1       Fast Food Restaurant   0.2
2         Italian Restaurant   0.2
3                  BBQ Joint   0.1
4           Tapas Restaurant   0.1
5          German Restaurant   0.1
6                 Steakhouse   0.0
7                 Restaurant   0.0
8         Seafood Restaurant   0.0
9  South American Restaurant   0.0


----Berazategui----
                       venue  freq
0       Fast Food Restaurant  0.50
1     Argentinian Restaurant  0.25
2         Chinese Restaurant  0.25
3           Sushi Restaurant  0.

9           Sushi Restaurant  0.00


----Punta Alta----
                       venue  freq
0                  BBQ Joint  0.75
1     Argentinian Restaurant  0.25
2         African Restaurant  0.00
3                 Steakhouse  0.00
4          Paella Restaurant  0.00
5        Peruvian Restaurant  0.00
6                 Restaurant  0.00
7         Seafood Restaurant  0.00
8  South American Restaurant  0.00
9         Spanish Restaurant  0.00


----Quilmes----
                    venue  freq
0              Restaurant  0.18
1  Argentinian Restaurant  0.18
2      Italian Restaurant  0.18
3               BBQ Joint  0.12
4    Fast Food Restaurant  0.12
5      Mexican Restaurant  0.06
6     American Restaurant  0.06
7                   Diner  0.06
8       German Restaurant  0.06
9              Steakhouse  0.00


----Reconquista----
                       venue  freq
0     Argentinian Restaurant  0.75
1       Fast Food Restaurant  0.25
2                 Steakhouse  0.00
3          Paella Restauran

In [26]:
def return_most_common_venues(row, num_top_venues):
    """
    Inputs: 'row' - pd.Series
            'num_top_venues' - int
    Outputs: 'row_categories_sorted.index.values[0:num_top_venues]' - a numpy.ndarray contains strings with the category name
    """
    list_ = []
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    for idx, item in enumerate(row_categories_sorted):
        if item != 0:
            list_.append(row_categories_sorted.index[idx])
    while len(list_) < 10:
        list_.append('-')
    return np.array(list_)[0:num_top_venues]

We make the frequencies into pandas DataFrame:

In [27]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['City']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
city_venues_sorted = pd.DataFrame(columns=columns)
city_venues_sorted['City'] = argentina_grouped['City']

for ind in np.arange(argentina_grouped.shape[0]):
    city_venues_sorted.iloc[ind, 1:] = return_most_common_venues(argentina_grouped.iloc[ind, :], num_top_venues)

city_venues_sorted.head()

City   1st Most Common Venue   2nd Most Common Venue  \
0          Azul               BBQ Joint                       -   
1  Bahía Blanca  Argentinian Restaurant      Italian Restaurant   
2   Berazategui    Fast Food Restaurant  Argentinian Restaurant   
3  Buenos Aires  Argentinian Restaurant              Restaurant   
4       Caseros  Argentinian Restaurant    Fast Food Restaurant   

  3rd Most Common Venue          4th Most Common Venue  \
0                     -                              -   
1  Fast Food Restaurant               Tapas Restaurant   
2    Chinese Restaurant                              -   
3    Italian Restaurant  Vegetarian / Vegan Restaurant   
4                     -                              -   

      5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                         -                     -                     -   
1         German Restaurant             BBQ Joint                     -   
2                         -                     -                     -   
3  Mediterranean Restaurant      Sushi Restaurant            Steakhouse   
4                         -                     -                     -   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0                     -                     -                      -  
1                     -                     -                      -  
2                     -                     -                      -  
3    Spanish Restaurant             BBQ Joint    Japanese Restaurant  
4                     -                     -                      -

## Using folium

We generate a df for ploting on a map, there are all the restaurants:

In [28]:
argentina_merged = argentina_restaurants.join(city_venues_sorted.set_index('City'), on='City')

argentina_merged.head()

City  City Latitude  City Longitude          restaurant  \
0  Buenos Aires      -34.60828      -58.372295            Pertutti   
2  Buenos Aires      -34.60828      -58.372295     Piazzolla Tango   
3  Buenos Aires      -34.60828      -58.372295             FuraiBo   
7  Buenos Aires      -34.60828      -58.372295     Elauge Hermanos   
8  Buenos Aires      -34.60828      -58.372295  Bidou de la Merced   

   restaurant Latitude  restaurant Longitude     restaurant Category  \
0           -34.609195            -58.373392  Argentinian Restaurant   
2           -34.606099            -58.374899        Theme Restaurant   
3           -34.610105            -58.372549     Japanese Restaurant   
7           -34.609276            -58.375499               BBQ Joint   
8           -34.605619            -58.373134              Restaurant   

   dist2center   1st Most Common Venue 2nd Most Common Venue  \
0   142.875942  Argentinian Restaurant            Restaurant   
2   340.024866  Argentinian Restaurant            Restaurant   
3   203.750072  Argentinian Restaurant            Restaurant   
7   313.927511  Argentinian Restaurant            Restaurant   
8   305.112268  Argentinian Restaurant            Restaurant   

  3rd Most Common Venue          4th Most Common Venue  \
0    Italian Restaurant  Vegetarian / Vegan Restaurant   
2    Italian Restaurant  Vegetarian / Vegan Restaurant   
3    Italian Restaurant  Vegetarian / Vegan Restaurant   
7    Italian Restaurant  Vegetarian / Vegan Restaurant   
8    Italian Restaurant  Vegetarian / Vegan Restaurant   

      5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0  Mediterranean Restaurant      Sushi Restaurant            Steakhouse   
2  Mediterranean Restaurant      Sushi Restaurant            Steakhouse   
3  Mediterranean Restaurant      Sushi Restaurant            Steakhouse   
7  Mediterranean Restaurant      Sushi Restaurant            Steakhouse   
8  Mediterranean Restaurant      Sushi Restaurant            Steakhouse   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0    Spanish Restaurant             BBQ Joint    Japanese Restaurant  
2    Spanish Restaurant             BBQ Joint    Japanese Restaurant  
3    Spanish Restaurant             BBQ Joint    Japanese Restaurant  
7    Spanish Restaurant             BBQ Joint    Japanese Restaurant  
8    Spanish Restaurant             BBQ Joint    Japanese Restaurant

Showing all the restaurants near the city center on a map, while our interesting category will be colored in **red**, and the other will be **blue**

In [33]:
map_argentina = folium.Map(location=[latitude, longitude], zoom_start=3.5)

# add markers to df
for lat, lng, city, pop, size in zip(df['lat'], df['lng'], df['city'], df['population_proper'], df['pop_norm']):
    label = '{},\n {}'.format(city, pop)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5 * size + 3,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_argentina)  
    
map_argentina

In [105]:
# create map
map_resaurants = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers to the map
markers_colors = []
for lat, lon, poi, r_lat, r_lon, r_name, dist, cat in zip(argentina_restaurants['City Latitude'], 
                                  argentina_restaurants['City Longitude'], 
                                  argentina_restaurants['City'], 
                                  argentina_restaurants['restaurant Latitude'],
                                  argentina_restaurants['restaurant Longitude'],
                                  argentina_restaurants['restaurant'],
                                  argentina_restaurants['dist2center'],
                                  argentina_restaurants['restaurant Category']):
    r_label = folium.Popup(r_name + '\n' + cat + '\n' + str(round(dist,2)) + '[m]' ,parse_html=True)
    if cat in ['Argentinian Restaurant', 'BBQ Joint']:
        folium.Marker(
            [r_lat, r_lon],
            icon=folium.Icon(color='red'),
            popup=r_label).add_to(map_resaurants)
    else:
        folium.Marker(
            [r_lat, r_lon],
            icon=folium.Icon(color='blue'),
            popup=r_label).add_to(map_resaurants)
    label = folium.Popup(str(poi), parse_html=True)
    folium.Marker(
        [lat, lon],
#         radius=10,
        icon=folium.Icon(color='black'),
        popup=label,
        fill=True,
        fill_opacity=0.7).add_to(map_resaurants)


# except:
#     print(lat, lon, poi, "------>   Has no near venues")
map_resaurants

Now we have all the restaurants in area within a radius of 1 km from every main city in Argentina, and we know which ones are local meat or BBQ restaurants.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new restaurants.

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting cities in Argentina that have low restaurant density near the city center, particularly those with low number of Argentinian restaurants. We will limit our analysis to area ~1km around city centers.

In first step we have collected the required **data: location and type (category) of every restaurant within 1km from the cities center**. We have also **identified local meat restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**restaurant density**' in every city - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (*and* no Argentinian restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without Argentinian restaurants in radius of 200 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

In [50]:
print('There are {:.2f} restaurants on average in every intersting city'.format(argentina_restaurants.groupby('City').count()['restaurant Category'].mean()))

There are 9.22 restaurants on average in every intersting city


In [52]:
matchers = ['argentinian','bbq', 'steakhouse']
matching = [s for s in list_of_venues if any(xs in s.lower() for xs in matchers)]
matching

['Argentinian Restaurant', 'BBQ Joint', 'Steakhouse']

In [109]:
argentina_local_restaurants = argentina_restaurants[argentina_restaurants['restaurant Category'].isin(matching)]
argentina_local_restaurants

City  City Latitude  City Longitude           restaurant  \
0     Buenos Aires      -34.60828      -58.372295             Pertutti   
7     Buenos Aires      -34.60828      -58.372295      Elauge Hermanos   
12    Buenos Aires      -34.60828      -58.372295       Puerto Cristal   
13    Buenos Aires      -34.60828      -58.372295                Chila   
15    Buenos Aires      -34.60828      -58.372295             Le Grill   
...            ...            ...             ...                  ...   
1025       Ushuaia      -54.80720      -68.304400       Casimiro Bigua   
1040       Ushuaia      -54.80720      -68.304400          Kénos Restó   
1041       Ushuaia      -54.80720      -68.304400     Parrila La Rueda   
1050          Azul      -36.78330      -59.850000  Parrilla El Carrito   
1055  Cruz del Eje      -30.73330      -64.800000            El Cardon   

      restaurant Latitude  restaurant Longitude     restaurant Category  \
0              -34.609195            -58.373392  Argentinian Restaurant   
7              -34.609276            -58.375499               BBQ Joint   
12             -34.610100            -58.365872  Argentinian Restaurant   
13             -34.611016            -58.366110  Argentinian Restaurant   
15             -34.607984            -58.366239  Argentinian Restaurant   
...                   ...                   ...                     ...   
1025           -54.807008            -68.302905  Argentinian Restaurant   
1040           -54.806395            -68.302388  Argentinian Restaurant   
1041           -54.805330            -68.301049              Steakhouse   
1050           -36.789406            -59.858032               BBQ Joint   
1055           -30.737260            -64.791606               BBQ Joint   

      dist2center  
0      142.875942  
7      313.927511  
12     622.758786  
13     643.369418  
15     556.453146  
...           ...  
1025    98.457383  
1040   157.358039  
1041   299.601331  
1050   986.483509  
1055   915.979304  

[207 rows x 8 columns]

We will now find the minimum distance from an Argentinian restuarant to the city center, for each city.
Then, we will detect the cities that have the longest distance from the first Argentinian restaurant.

In [89]:
min_dist = argentina_restaurants[argentina_restaurants['restaurant Category'].isin(matching)]
min_dist = min_dist.groupby('City').min('dist2center').sort_values('dist2center', ascending=False)
min_dist

City Latitude  City Longitude  \
City                                                        
Azul                           -36.783300      -59.850000   
Caseros                        -34.616700      -58.533300   
Cruz del Eje                   -30.733300      -64.800000   
Pergamino                      -33.883600      -60.566900   
Río Gallegos                   -51.633300      -69.233300   
Paraná                         -31.744400      -60.517500   
Comodoro Rivadavia             -45.866700      -67.500000   
San Salvador de Jujuy          -24.185600      -65.299400   
Florencio Varela               -34.816700      -58.383300   
Berazategui                    -34.767900      -58.213300   
Lanús                          -34.700000      -58.400000   
La Banda                       -27.733300      -64.250000   
Corrientes                     -27.483300      -58.816700   
Puerto Madryn                  -42.773000      -65.036600   
Concordia                      -31.392200      -58.016900   
Gualeguaychú                   -33.007800      -58.511100   
Quilmes                        -34.716700      -58.266700   
Goya                           -29.133300      -59.250000   
Villa María                    -32.410300      -63.231400   
San Ramón de la Nueva Orán     -23.136100      -64.322200   
San Nicolás de los Arroyos     -33.333300      -60.216700   
Godoy Cruz                     -32.916700      -68.833300   
Santa Fe                       -31.633300      -60.700000   
Resistencia                    -27.451400      -58.986700   
Morón                          -34.650000      -58.616700   
Pilar                          -34.458800      -58.914200   
Neuquén                        -38.957300      -68.045500   
Córdoba                        -31.416700      -64.183300   
Bahía Blanca                   -38.716700      -62.266700   
San Luis                       -33.299400      -66.339200   
Villa Mercedes                 -33.666700      -65.466700   
La Rioja                       -29.413100      -66.855800   
Mar del Plata                  -38.000000      -57.550000   
Merlo                          -34.665300      -58.727500   
Punta Alta                     -38.880000      -62.080000   
Buenos Aires                   -34.608280      -58.372295   
Mendoza                        -32.889712      -68.844542   
Concepción del Uruguay         -32.483300      -58.233300   
Posadas                        -27.366700      -55.896900   
San Carlos de Bariloche        -41.133402      -71.310240   
Ushuaia                        -54.807200      -68.304400   
Salta                          -24.788300      -65.410600   
Reconquista                    -29.144300      -59.643800   
Rosario                        -32.957500      -60.639400   
Catamarca                      -28.468600      -65.779200   

                            restaurant Latitude  restaurant Longitude  \
City                                                                    
Azul                                 -36.789406            -59.858032   
Caseros                              -34.612975            -58.523665   
Cruz del Eje                         -30.737260            -64.791606   
Pergamino                            -33.888480            -60.574759   
Río Gallegos                         -51.627887            -69.224620   
Paraná                               -31.745387            -60.526375   
Comodoro Rivadavia                   -45.868050            -67.492160   
San Salvador de Jujuy                -24.188272            -65.308294   
Florencio Varela                     -34.815401            -58.375228   
Berazategui                          -34.762381            -58.208570   
Lanús                                -34.706626            -58.394257   
La Banda                             -27.731117            -64.243148   
Corrientes                           -27.477575            -58.821811   
Puerto Madryn                        -42.767583            -65.03

Let's crete a map showing heatmap / density of restaurants.

In [111]:
restaurant_latlon = [[r_lat, r_lon] for r_lat, r_lon in zip(argentina_restaurants['restaurant Latitude'],
                                                            argentina_restaurants['restaurant Longitude'])]
local_restaurant_latlon = [[r_lat, r_lon] for r_lat, r_lon in zip(argentina_local_restaurants['restaurant Latitude'],
                                                            argentina_local_restaurants['restaurant Longitude'])]

In [124]:
from folium import plugins
from folium.plugins import HeatMap

arg_latlon = [latitude, longitude]
map_argentina = folium.Map(location=arg_latlon, zoom_start=5)
folium.TileLayer('cartodbpositron').add_to(map_argentina) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlon).add_to(map_argentina)

for lat, lng, city, pop, size in zip(df['lat'], df['lng'], df['city'], df['population_proper'], df['pop_norm']):
    label = '{},\n {:d} people'.format(city, int(pop))
    label = folium.Popup(label, parse_html=True)
    folium.Marker(
        [lat, lng],
        popup=label,
        color='blue',
        parse_html=False).add_to(map_argentina) 


map_argentina



In [121]:
map_argentina = folium.Map(location=[latitude, longitude], zoom_start=5)
folium.TileLayer('cartodbpositron').add_to(map_argentina) #cartodbpositron cartodbdark_matter
HeatMap(local_restaurant_latlon).add_to(map_argentina)

for lat, lng, city, pop, size in zip(df['lat'], df['lng'], df['city'], df['population_proper'], df['pop_norm']):
    label = '{},\n {} people'.format(city, pop)
    label = folium.Popup(label, parse_html=True)
    folium.Marker(
        [lat, lng],
        popup=label,
        color='blue',
        parse_html=False).add_to(map_argentina) 
    
map_argentina

#### Cordoba

For an example, we will focus on a main city in Argentina - **Cordoba**

In [312]:
address = 'cordoba, argentina'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Córdoba are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Cordoba are -31.4173391, -64.183319.


In [315]:
cordoba_res = argentina_restaurants[argentina_restaurants['City'] == 'Córdoba']
cordoba_local_res = argentina_local_restaurants[argentina_local_restaurants['City'] == 'Córdoba']

print('There are {} local restaurants in Córdoba, {:.1f}% from all the restaurants near the center ({})'.format(cordoba_local_res.shape[0],
                                                                                                            cordoba_local_res.shape[0]/cordoba_res.shape[0]*100,
                                                                                                                 cordoba_res.shape[0]))

There are 9 local restaurants in Córdoba, 22.0% from all the restaurants near the center (41)


In [318]:
cordoba_coor = [latitude, longitude]

# coor = [bar_coor[0], bar_coor[1]]
# create map
map_cordoba = folium.Map(location=cordoba_coor, zoom_start=15)

# add markers to the map
for lat, lon, poi, r_lat, r_lon, r_name, dist, cat in zip(cordoba_res['City Latitude'], 
                                  cordoba_res['City Longitude'], 
                                  cordoba_res['City'], 
                                  cordoba_res['restaurant Latitude'],
                                  cordoba_res['restaurant Longitude'],
                                  cordoba_res['restaurant'],
                                  cordoba_res['dist2center'],
                                  cordoba_res['restaurant Category']):
    r_label = folium.Popup(r_name + '\n' + cat + '\n' + str(round(dist,2)) + '[m]' ,parse_html=True)
    if cat in ['Argentinian Restaurant', 'BBQ Joint']:
        folium.Marker(
            [r_lat, r_lon],
            icon=folium.Icon(color='red'),
            popup=r_label).add_to(map_cordoba)
    else:
        folium.Marker(
            [r_lat, r_lon],
            icon=folium.Icon(color='blue'),
            popup=r_label).add_to(map_cordoba)
    label = folium.Popup(str(poi), parse_html=True)
    folium.Marker(
        [lat, lon],
#         radius=10,
        icon=folium.Icon(color='black'),
        popup=label,
        fill=True,
        fill_opacity=0.7).add_to(map_cordoba)
folium.Circle(cordoba_coor, radius=300, fill=False, color='white').add_to(map_cordoba)
folium.Circle(cordoba_coor, radius=600, fill=False, color='white').add_to(map_cordoba)
folium.Circle(cordoba_coor, radius=1000, fill=False, color='white').add_to(map_cordoba)
map_cordoba

In [224]:
from utm import from_latlon as latlon_to_xy
from utm import to_latlon as xy_to_latlon

In [149]:
# !pip install shapely
import shapely.geometry

import math

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)



In [322]:
print('Coordinate transformation check')
print('-------------------------------')
print('Cordoba center, latitude={} longitude={}'.format(cordoba_coor[0], cordoba_coor[1]))
x, y, num, numl = latlon_to_xy(cordoba_coor[0], cordoba_coor[1])
print('Cordoba center UTM X={}, Y={}'.format(x, y))
la, lo = xy_to_latlon(x, y, num, numl)
print('Cordoba center, latitude={}, longitude={}'.format(la, lo))

Coordinate transformation check
-------------------------------
Cordoba center, latitude=-31.4173391 longitude=-64.183319
Cordoba center UTM X=387524.4895308789, Y=6523539.422501789
Cordoba center, latitude=-31.41733909955648, longitude=-64.18331900000022


In [324]:
cordoba_center_x, cordoba_center_y, num, numl = latlon_to_xy(cordoba_coor[0], cordoba_coor[1])

In [482]:
roi_x_min = cordoba_center_x - 1000
roi_y_max = cordoba_center_y + 500
roi_width = 2500
roi_height = 2500
roi_center_x = cordoba_center_x#roi_x_min + 2500
roi_center_y = cordoba_center_y#roi_y_max - 2500
roi_center_lat, roi_center_lon = xy_to_latlon(roi_center_x, roi_center_y, num, numl)
roi_center = [roi_center_lat, roi_center_lon]

In [483]:
roi_center

[-31.41733909955648, -64.18331900000022]

In [484]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lat, lon = xy_to_latlon(x, y, num, numl)
            roi_longitudes.append(lon)
            roi_latitudes.append(lat)
            roi_xs.append(x)
            roi_ys.append(y)

In [485]:
roi_ys

[6521039.422501789,
 6521039.422501789,
 6521126.025042168,
 6521126.025042168,
 6521126.025042168,
 6521126.025042168,
 6521126.025042168,
 6521126.025042168,
 6521126.025042168,
 6521126.025042168,
 6521126.025042168,
 6521126.025042168,
 6521126.025042168,
 6521126.025042168,
 6521126.025042168,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521212.627582546,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,
 6521299.230122925,


In [486]:
print(len(roi_latitudes), 'candidate areas generated.')

1705 candidate areas generated.


Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Argentinian restaurant**.

In [487]:
cordoba_res['restaurant']

100                                Sibaris
101                    Casa Galan restoran
105                    La Cocina de Fazzio
106                            El Papagayo
108                            Estacion 27
109                                   Qara
111                            Burger King
112                          Cientovolando
113                        Solar de Tejeda
114                                  Betos
118                                  Díran
120                               La Mamma
123                                  Festo
124                              SushiClub
129               Alcorta - Carnes y Vinos
130                            Burger King
133                             Mandarina!
134                 Siamo Cio Che Mangiamo
136                 La Zete Comidas Arabes
137                                   Lelé
138                         Johnny B. Good
139                   La Entrada del Olmos
140                         Natural Mystic
142        

In [488]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res, lat, lon in zip(restaurants['restaurant'], restaurants['restaurant Latitude'], restaurants['restaurant Longitude']):
        res_x, res_y = latlon_to_xy(lat, lon)[0:2]
        d = calc_xy_distance(x, y, res_x, res_y)
#         print(d)
        if d<=radius:
            count += 1
#     print(count)
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res, lat, lon in zip(restaurants['restaurant'], restaurants['restaurant Latitude'], restaurants['restaurant Longitude']):
        res_x, res_y = latlon_to_xy(lat, lon)[0:2]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_local_distances = []


print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
#     print(xy_to_latlon(x,y,num,numl))
    count = count_restaurants_nearby(x, y, cordoba_res.loc[:,['restaurant','restaurant Latitude','restaurant Longitude']], radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, cordoba_res.loc[:,['restaurant','restaurant Latitude','restaurant Longitude']])
    roi_local_distances.append(distance)
print('done.')

Generating data on location candidates... done.


In [489]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Local restaurant':roi_local_distances})

df_roi_locations

Latitude  Longitude              X             Y  Restaurants nearby  \
0    -31.439886 -64.184128  387474.489531  6.521039e+06                   0   
1    -31.439896 -64.183076  387574.489531  6.521039e+06                   0   
2    -31.439051 -64.189905  386924.489531  6.521126e+06                   0   
3    -31.439061 -64.188853  387024.489531  6.521126e+06                   0   
4    -31.439071 -64.187801  387124.489531  6.521126e+06                   0   
...         ...        ...            ...           ...                 ...   
1700 -31.395371 -64.181992  387624.489531  6.525976e+06                   0   
1701 -31.395381 -64.180940  387724.489531  6.525976e+06                   0   
1702 -31.395391 -64.179888  387824.489531  6.525976e+06                   0   
1703 -31.395400 -64.178837  387924.489531  6.525976e+06                   0   
1704 -31.395410 -64.177785  388024.489531  6.525976e+06                   0   

      Distance to Local restaurant  
0                      1638.397677  
1                      1638.292668  
2                      1663.611145  
3                      1630.109799  
4                      1602.159128  
...                            ...  
1700                   1598.967422  
1701                   1590.362635  
1702                   1588.020718  
1703                   1591.969313  
1704                   1602.161910  

[1705 rows x 6 columns]

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no local restaurants in radius of 300 meters**.

In [496]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_local_distance = np.array(df_roi_locations['Distance to Local restaurant']>=300)
print('Locations with no local restaurants within 300m:', good_local_distance.sum())

good_locations = np.logical_and(good_res_count, good_local_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]

Locations with no more than two restaurants nearby: 1576
Locations with no local restaurants within 300m: 1332
Locations with both conditions met: 1332


In [495]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_cordoba = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_cordoba)
HeatMap(restaurant_latlon).add_to(map_cordoba)
folium.Circle(roi_center, radius=1000, color='white', fill=True, fill_opacity=0.6).add_to(map_cordoba)
folium.Marker([cordoba_coor[0], cordoba_coor[1]]).add_to(map_cordoba)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_cordoba) 
#     print(lat, lon)
map_cordoba

Looking good. We now have a bunch of locations fairly close to Cordoba's center, and we know that each of those locations has no more than two restaurants in radius of 300m, and no local restaurant closer than 250m. Any of those locations is a potential candidate for a new Argentinian restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [410]:
map_cordoba = folium.Map(location=roi_center, zoom_start=14)

HeatMap(good_locations, radius=25).add_to(map_cordoba)
folium.Marker(cordoba_coor).add_to(map_cordoba)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_cordoba)
map_cordoba

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Argentinian restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [499]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_latlon(cc[0], cc[1], num, numl) for cc in kmeans.cluster_centers_]

map_cordoba = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_cordoba)
HeatMap(restaurant_latlon).add_to(map_cordoba)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_cordoba)
folium.Marker(cordoba_coor).add_to(map_cordoba)
for lat, lon in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_cordoba) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_cordoba)
map_cordoba

Our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [503]:
map_cordoba = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(cordoba_coor).add_to(map_cordoba)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_cordoba)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_cordoba)
for lat, lon in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_cordoba) 
map_cordoba

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [504]:
location = geolocator.geocode("cordoba, argentina")
(location.latitude, location.longitude)
address = geolocator.reverse((location.latitude, location.longitude))
address.raw

{'place_id': 20005740,
 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright',
 'osm_type': 'way',
 'osm_id': 319622291,
 'lat': '-31.417371308163265',
 'lon': '-64.18333005102042',
 'display_name': '93, San Jerónimo, Centro, Córdoba, Municipio de Córdoba, Pedanía Capital, Departamento Capital, Córdoba, X5000, Argentina',
 'address': {'house_number': '93',
  'road': 'San Jerónimo',
  'quarter': 'Centro',
  'city': 'Córdoba',
  'municipality': 'Municipio de Córdoba',
  'county': 'Pedanía Capital',
  'state_district': 'Departamento Capital',
  'state': 'Córdoba',
  'postcode': 'X5000',
  'country': 'Argentina',
  'country_code': 'ar'},
 'boundingbox': ['-31.417421308163',
  '-31.417321308163',
  '-64.18338005102',
  '-64.18328005102']}

In [505]:
def get_address(lat, lon):
    address = geolocator.reverse((lat, lon))
    try:
        full_address = address.raw['address']['road'] + ', ' + address.raw['address']['house_number'] + ' ' + address.raw['address']['city'] 
    except:
        print('Has no house number')
        full_address = address.raw['address']['road'] + ', ' + address.raw['address']['city'] 
    return full_address

In [506]:
print(geolocator.reverse((-31.39776755102632, -64.18063517356521)).raw)

{'place_id': 7737979, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright', 'osm_type': 'node', 'osm_id': 891516363, 'lat': '-31.3980509', 'lon': '-64.1803024', 'display_name': 'Alta Córdoba, Jerónimo Luis de Cabrera, Alta Córdoba, Córdoba, Municipio de Córdoba, Pedanía Capital, Departamento Capital, Córdoba, X5001, Argentina', 'address': {'railway': 'Alta Córdoba', 'road': 'Jerónimo Luis de Cabrera', 'suburb': 'Alta Córdoba', 'city': 'Córdoba', 'municipality': 'Municipio de Córdoba', 'county': 'Pedanía Capital', 'state_district': 'Departamento Capital', 'state': 'Córdoba', 'postcode': 'X5001', 'country': 'Argentina', 'country_code': 'ar'}, 'boundingbox': ['-31.4030509', '-31.3930509', '-64.1853024', '-64.1753024']}


In [507]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lat, lon in cluster_centers:
#     print(lat,lon)
    addr = get_address(lat, lon)
    candidate_area_addresses.append(addr)    
    x, y = latlon_to_xy(lat, lon)[0:2]
    d = calc_xy_distance(x, y, cordoba_center_x, cordoba_center_y)
    print('{}{} => {:.1f}km from Cordoba center'.format(addr, ' '*(50-len(addr)), d/1000))

Addresses of centers of areas recommended for further analysis

Bahía Blanca, 899 Córdoba                          => 1.3km from Cordoba center
Has no house number
Avenida Ciudad de Valparaíso, Córdoba              => 2.0km from Cordoba center
General Paz, 1582 Córdoba                          => 2.0km from Cordoba center
Jacinto Ríos, 1334 Córdoba                         => 2.1km from Cordoba center
Uruguay, 188 Córdoba                               => 2.1km from Cordoba center
Agustín Garzón, 1636 Córdoba                       => 2.1km from Cordoba center
Has no house number
Avenida Intendente Mestre Norte, Córdoba           => 1.4km from Cordoba center
Avenida Pueyrredón, 176 Córdoba                    => 1.3km from Cordoba center
Avenida Intendente Mestre Norte, 444 Córdoba       => 1.3km from Cordoba center
Has no house number
Manuel Pizarro, Córdoba                            => 2.2km from Cordoba center
Oncativo, 1579 Córdoba                             => 2.1km from Cordoba cen

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Argentinian restaurants nearby, all zones being fairly close to city center (all less than 3km from the center, and about half of those less than 1.5km). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. 

In [508]:
map_cordoba = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(cordoba_coor, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_cordoba)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    print(addr)
    folium.Marker([lonlat[0], lonlat[1]], popup=addr).add_to(map_cordoba) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_cordoba)
map_cordoba

Bahía Blanca, 899 Córdoba
Avenida Ciudad de Valparaíso, Córdoba
General Paz, 1582 Córdoba
Jacinto Ríos, 1334 Córdoba
Uruguay, 188 Córdoba
Agustín Garzón, 1636 Córdoba
Avenida Intendente Mestre Norte, Córdoba
Avenida Pueyrredón, 176 Córdoba
Avenida Intendente Mestre Norte, 444 Córdoba
Manuel Pizarro, Córdoba
Oncativo, 1579 Córdoba
Avenida Madrid, 2102 Córdoba
Avenida 24 de Septiembre, 843 Córdoba
Faustino Allende, 832 Córdoba
Avenida Deodoro Roca, Córdoba


The neighborhood of Güemes will be a good place to be. It is a cool place where visitors spend at least an afternoon. Filled with fancy local bars, trendy cafes, and restaurants, this neighborhood will keep you busy. Güemes is a bohemian style, probably the hippiest and coolest place in Cordoba. Muy Güemes offers many boutiques to see, delicious food joints to try and shopping areas to check out. Strolling down the streets or sitting in a restaurant in Güemes is a refreshing activity in this very alive neighborhood. [https://skyticket.com/guide/2847#articleHead_7]

## Results and Discussion <a name="results"></a>

Our analysis shows that there are pockets of low restaurant density fairly close to city center of Cordoba. Highest concentration of restaurants was detected 600-900 meters from the center, so we focused our attention to areas at the outer radius, but still close - about 1 km from the center - corresponding to borough Guemes south-west corner of center. Another borough was identified as potentially interesting (Nueva Cordoba), but our attention was focused on Guemes which offer a combination of popularity among tourists, closeness to city center, strong socio-economic dynamics *and* pockets of low restaurant density.

After directing our attention to this more narrow area of interest we created a dense grid of location candidates (spaced 100m apart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Argentinian meat restaurant closer than 300m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Argentinian restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Cordoba center but not crowded with existing restaurants (particularly Argentinian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

The purpose of this project was to identify Cities in Argentina that has good potential to open new Argentinian meat restaurant. Then we focused our analysis to the city of Cordoba, in order to find areas close to center with low number of restaurants (particularly Argentinian restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Argentinian meat restaurant. By calculating restaurant density distribution from Foursquare data we have first identified cities that justify further analysis (we continued with Cordoba, but we could choose other city as well), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decision on optimal restaurant location will be made by stakeholders based on specific characteristics of neighbourhoods  and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighbourhoods  etc.